In [1]:
import matplotlib.pyplot as plt
import seaborn as sn
from sklearn.preprocessing import MinMaxScaler
import pandas as pd
import numpy as np
import tensorflow as tf
tfk = tf.keras
tf.keras.backend.set_floatx("float64")
import tensorflow_probability as tfp
tfd = tfp.distributions
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import IsolationForest
from keras import backend as K
from keras.callbacks import EarlyStopping
%config InlineBackend.figure_format = 'retina'
import pandas as pd
%matplotlib inline
from keras import activations, initializers
from keras.layers import Layer
import tensorflow as tf
from tensorflow.keras.layers import Input
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.layers import Input, Dense, Flatten, BatchNormalization, Activation, LeakyReLU
from tensorflow_probability.python.layers import DistributionLambda
import tensorflow_probability as tfp
tfd = tfp.distributions

%matplotlib inline

Using TensorFlow backend.


In [2]:
noise = 1
def neg_log_likelihood_with_dist(y_true, y_pred, sigma = noise):
    return -tf.reduce_mean(y_pred.log_prob(y_true))

In [3]:
def mixture_prior_params(sigma_1, sigma_2, pi, return_sigma=False):
    params = K.variable([sigma_1, sigma_2, pi], name='mixture_prior_params')
    sigma = np.sqrt(pi * sigma_1 ** 2 + (1 - pi) * sigma_2 ** 2)
    return params, sigma
  
def log_mixture_prior_prob(w):
    comp_1_dist = tf.distributions.Normal(0.0, prior_params[0])
    comp_2_dist = tf.distributions.Normal(0.0, prior_params[1])
    comp_1_weight = prior_params[2]
    return K.log(comp_1_weight * comp_1_dist.prob(w) + (1 - comp_1_weight) * comp_2_dist.prob(w))
  
# Mixture prior parameters shared across DenseVariational layer instances
prior_params, prior_sigma = mixture_prior_params(sigma_1=1.0, sigma_2=0.1, pi=0.2)

In [4]:
# Specify the surrogate posterior over `keras.layers.Dense` `kernel` and `bias`.
def  posterior_mean_field(kernel_size, bias_size=0, dtype=None):
    n = kernel_size + bias_size
    c = np.log(np.expm1(1.))
    return tf.keras.Sequential(
        [tfp.layers.VariableLayer(2 * n, dtype=dtype),
        tfp.layers.DistributionLambda(lambda t: tfd.Independent(
            tfd.Normal(loc=t[..., :n], scale=1e-5 + tf.nn.softplus(c + t[..., n:])),
            reinterpreted_batch_ndims=1)),
])

# Specify the prior over `keras.layers.Dense` `kernel` and `bias`.
def prior_trainable(kernel_size, bias_size=0, dtype=None):
    n = kernel_size + bias_size
    return tf.keras.Sequential([
        tfp.layers.VariableLayer(n, dtype=dtype),
        tfp.layers.DistributionLambda(lambda t: tfd.Independent(
            tfd.Normal(loc=t, scale=1),
            reinterpreted_batch_ndims=1)),
])

In [5]:
df = pd.read_csv('scaled_dummied_task.csv')
#df.head()

In [6]:
permuts = pd.read_csv('../HolyGrail/permutations.csv')

In [7]:
x_train = df.drop('Target', axis = 1)
y_train = df['Target']

In [8]:
n_epochs = 50000
lr = 5e-3
batch_size = x_train.shape[0]

In [12]:
def implement_wape(ys, preds):
    numer8 = np.sum(np.abs(np.array(ys) - np.array(preds)))
    w = (numer8)/np.sum(np.abs(ys))
    return w

In [ ]:
from hyperopt import fmin, tpe, hp, STATUS_OK, Trials
from sklearn.metrics import roc_auc_score
import sys
train_size = len(x_train)
X = []
y = []
X_val = []
y_val = []

space = {'choice': hp.choice('num_layers',
                             [{'layers':'two', },
                              {'layers':'three', 
                               'units3': hp.choice('units3', [32, 64])
                              }
                             ]),
         'units1': hp.choice('units1', [16, 32, 64]),
         'units2': hp.choice('units2', [16, 32, 64]),
         'optimizer': hp.choice('optimizer',['adadelta','adam','rmsprop']),
        }

def f_nn(params):   

    print ('Params testing: ', params)
    model_in = Input(shape=(x_train.shape[1],))
    x = tfp.layers.DenseVariational(int('{}'.format(params['units1'])), posterior_mean_field, prior_trainable, kl_weight=1/train_size)(model_in)
    x = LeakyReLU(0.1)(x)
    x = tfp.layers.DenseVariational(int('{}'.format(params['units2'])), posterior_mean_field, prior_trainable, kl_weight=1/train_size)(x)
    x = LeakyReLU(0.1)(x)
    
    if params['choice']['layers']== 'three':
        x = tfp.layers.DenseVariational(int('{}'.format(params['choice']['units3'])), posterior_mean_field, prior_trainable, kl_weight=1/train_size)(x)
        x = LeakyReLU(0.1)(x) 
    
    model_out_loc = tfp.layers.DenseVariational(1, posterior_mean_field, prior_trainable, kl_weight=1/train_size)(x)
    model_out_scale = tfp.layers.DenseVariational(1, posterior_mean_field, prior_trainable, kl_weight=1/train_size)(x)
    model_out = DistributionLambda(lambda t: tfd.Normal(loc=t[0],
                                                        scale=1e-7 + tf.math.softplus(1e-3 * t[1])))([model_out_loc,
                                                                                                      model_out_scale])
    model = Model(model_in, model_out)
    model.compile(loss=neg_log_likelihood_with_dist, optimizer=params['optimizer'], metrics=['mse'])
    early_stop = EarlyStopping(monitor='mse', min_delta = 0, patience=1000, mode='auto')
    model.fit(x_train, y_train, epochs = n_epochs, batch_size = batch_size, verbose = 0, callbacks = [early_stop])

    y_pred_list = []
    for i in range(len(x_train)):
        tensor = tf.constant([x_train.iloc[i]], dtype='float32')
        pred_list = []
        for j in range(500):
            y_pred = model.predict(tensor)
            pred_list.append(y_pred)
        y_pred_list.append(pred_list)

    y_means = np.mean(y_pred_list, axis = 1)
    y_means = y_means.reshape(len(x_train),)
    wape = implement_wape(y_means, y_train)
    print('WAPE: {}' .format(wape))
    return wape
    
trials = Trials()
best = fmin(f_nn, space, algo=tpe.suggest, max_evals=5, trials=trials)
print('best: ', best)

('Params testing: ', {'units1': 16, 'units2': 64, 'optimizer': 'adadelta', 'choice': {'layers': 'two'}})
  0%|          | 0/5 [00:00<?, ?trial/s, best loss=?]WARNING:tensorflow:Falling back from v2 loop because of error: Failed to find data adapter that can handle input: <class 'pandas.core.frame.DataFrame'>, <type 'NoneType'>
Train on 600 samples                                 
Epoch 1/50000                                        
600/600 [==============================]             
 - 1s 2ms/sample - loss: 2526.7878 - mse: 2247.2878  

Epoch 2/50000                                        
600/600 [==============================]             
 - 0s 19us/sample - loss: 2128.2695 - mse: 2112.6963 

Epoch 3/50000                                        
600/600 [==============================]             
 - 0s 20us/sample - loss: 8575.2285 - mse: 8832.0303 

Epoch 4/50000                                        
600/600 [==============================]             
 - 0s 18us/sample - 

 - 0s 18us/sample - loss: 620.4441 - mse: 585.4493   

Epoch 99/50000                                       
600/600 [==============================]             
 - 0s 20us/sample - loss: 6135.9644 - mse: 5609.5088 

Epoch 100/50000                                      
600/600 [==============================]             
 - 0s 22us/sample - loss: 1894.4667 - mse: 1781.3995 

Epoch 101/50000                                      
600/600 [==============================]             
 - 0s 19us/sample - loss: 4149.6865 - mse: 4421.7896 

Epoch 102/50000                                      
600/600 [==============================]             
 - 0s 20us/sample - loss: 6981.9424 - mse: 7204.1108 

Epoch 103/50000                                      
600/600 [==============================]             
 - 0s 18us/sample - loss: 373.8364 - mse: 351.6891   

Epoch 104/50000                                      
600/600 [==============================]             
 - 0s 18us/sample - lo

 - 0s 17us/sample - loss: 1522.5818 - mse: 1497.5054 

Epoch 199/50000                                      
600/600 [==============================]             
 - 0s 22us/sample - loss: 2034.7184 - mse: 2072.1646 

Epoch 200/50000                                      
600/600 [==============================]             
 - 0s 20us/sample - loss: 6961.2363 - mse: 5892.7593 

Epoch 201/50000                                      
600/600 [==============================]             
 - 0s 20us/sample - loss: 2648.3230 - mse: 2648.4668 

Epoch 202/50000                                      
600/600 [==============================]             
 - 0s 19us/sample - loss: 432.4214 - mse: 431.0106   

Epoch 203/50000                                      
600/600 [==============================]             
 - 0s 18us/sample - loss: 1012.9089 - mse: 1013.8654 

Epoch 204/50000                                      
600/600 [==============================]             
 - 0s 21us/sample - lo

 - 0s 19us/sample - loss: 439.0595 - mse: 439.9270   

Epoch 299/50000                                      
600/600 [==============================]             
 - 0s 18us/sample - loss: 1083.6417 - mse: 1049.7500 

Epoch 300/50000                                      
600/600 [==============================]             
 - 0s 18us/sample - loss: 2979.2083 - mse: 2621.1399 

Epoch 301/50000                                      
600/600 [==============================]             
 - 0s 21us/sample - loss: 526.2123 - mse: 500.8653   

Epoch 302/50000                                      
600/600 [==============================]             
 - 0s 18us/sample - loss: 2123.1733 - mse: 2325.9873 

Epoch 303/50000                                      
600/600 [==============================]             
 - 0s 19us/sample - loss: 740.0156 - mse: 728.8800   

Epoch 304/50000                                      
600/600 [==============================]             
 - 0s 20us/sample - lo

 - 0s 19us/sample - loss: 2352.6313 - mse: 2058.9280 

Epoch 399/50000                                      
600/600 [==============================]             
 - 0s 20us/sample - loss: 980.3629 - mse: 979.2379   

Epoch 400/50000                                      
600/600 [==============================]             
 - 0s 19us/sample - loss: 659.6692 - mse: 620.0729   

Epoch 401/50000                                      
600/600 [==============================]             
 - 0s 21us/sample - loss: 5480.3765 - mse: 5580.4834 

Epoch 402/50000                                      
600/600 [==============================]             
 - 0s 20us/sample - loss: 1006.7550 - mse: 923.8441  

Epoch 403/50000                                      
600/600 [==============================]             
 - 0s 21us/sample - loss: 1617.5096 - mse: 1665.8309 

Epoch 404/50000                                      
600/600 [==============================]             
 - 0s 20us/sample - lo

...

 - 0s 22us/sample - loss: 1525.3315 - mse: 1335.7910 

Epoch 28399/50000                                    
600/600 [==============================]             
 - 0s 20us/sample - loss: 2372.0193 - mse: 2203.9797 

Epoch 28400/50000                                    
600/600 [==============================]             
 - 0s 22us/sample - loss: 4729.5083 - mse: 4562.9756 

Epoch 28401/50000                                    
600/600 [==============================]             
 - 0s 20us/sample - loss: 589.7898 - mse: 578.5631   

Epoch 28402/50000                                    
600/600 [==============================]             
 - 0s 20us/sample - loss: 1788.2925 - mse: 1654.0385 

Epoch 28403/50000                                    
600/600 [==============================]             
 - 0s 20us/sample - loss: 1831.9921 - mse: 1749.8129 

Epoch 28404/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - lo

 - 0s 21us/sample - loss: 3673.7388 - mse: 3557.8259 

Epoch 28499/50000                                    
600/600 [==============================]             
 - 0s 22us/sample - loss: 2701.3477 - mse: 2754.0469 

Epoch 28500/50000                                    
600/600 [==============================]             
 - 0s 20us/sample - loss: 750.3872 - mse: 714.7030   

Epoch 28501/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - loss: 1876.9225 - mse: 1730.5735 

Epoch 28502/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - loss: 356.2989 - mse: 338.7549   

Epoch 28503/50000                                    
600/600 [==============================]             
 - 0s 19us/sample - loss: 331.4628 - mse: 321.7093   

Epoch 28504/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - lo

 - 0s 21us/sample - loss: 467.2370 - mse: 453.4495   

Epoch 28599/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - loss: 435.0539 - mse: 440.3989   

Epoch 28600/50000                                    
600/600 [==============================]             
 - 0s 22us/sample - loss: 2531.3875 - mse: 2591.7117 

Epoch 28601/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - loss: 428.4231 - mse: 399.5677   

Epoch 28602/50000                                    
600/600 [==============================]             
 - 0s 22us/sample - loss: 1226.0931 - mse: 1155.0527 

Epoch 28603/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - loss: 1674.1632 - mse: 1594.0099 

Epoch 28604/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - lo

 - 0s 22us/sample - loss: 817.1584 - mse: 750.9863   

Epoch 28699/50000                                    
600/600 [==============================]             
 - 0s 22us/sample - loss: 370.7730 - mse: 371.5844   

Epoch 28700/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - loss: 378.1212 - mse: 376.1839   

Epoch 28701/50000                                    
600/600 [==============================]             
 - 0s 22us/sample - loss: 359.1649 - mse: 329.4505   

Epoch 28702/50000                                    
600/600 [==============================]             
 - 0s 20us/sample - loss: 2187.1267 - mse: 2008.2875 

Epoch 28703/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - loss: 2640.7510 - mse: 2466.5491 

Epoch 28704/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - lo

 - 0s 21us/sample - loss: 1271.0699 - mse: 1202.5316 

Epoch 28799/50000                                    
600/600 [==============================]             
 - 0s 22us/sample - loss: 423.7200 - mse: 422.7939   

Epoch 28800/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - loss: 1757.4871 - mse: 1683.1793 

Epoch 28801/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - loss: 770.6498 - mse: 725.3969   

Epoch 28802/50000                                    
600/600 [==============================]             
 - 0s 22us/sample - loss: 1284.2234 - mse: 1278.3943 

Epoch 28803/50000                                    
600/600 [==============================]             
 - 0s 21us/sample - loss: 259.4150 - mse: 245.8020   

Epoch 28804/50000                                    
600/600 [==============================]             
 - 0s 22us/sample - lo

In [ ]:
y_pred_list = []
for i in range(len(permuts)):
    tensor = tf.constant([permuts.iloc[i]], dtype='float32')
    pred_list = []
    for j in range(5):
        y_pred = model.predict(tensor)
        pred_list.append(y_pred)
    y_pred_list.append(pred_list)

In [ ]:
y_means = np.mean(y_pred_list, axis = 1)
y_sigmas = np.std(y_pred_list, axis = 1)

In [ ]:
y_sigmas = y_sigmas.reshape(len(permuts),)
y_means = y_means.reshape(len(permuts),)

In [ ]:
idx = range(len(permuts))
plt.figure(figsize = (15, 7))
plt.plot(idx, y_means, 'r-', label='Predictive mean');
plt.fill_between(idx, y_means + 2 * y_sigmas,
                 y_means - 2 * y_sigmas, alpha=0.5)
plt.legend()
plt.title('Predictions');